_Lambda School Data Science, Unit 2_
 
# Regression & Classification Sprint Challenge

To demonstrate mastery on your Sprint Challenge, do all the required, numbered instructions in this notebook.

To earn a score of "3", also do all the stretch goals.

You are permitted and encouraged to do as much data exploration as you want.

### Part 1, Classification
- 1.1. Begin with baselines for classification
- 1.2. Do train/test split. Arrange data into X features matrix and y target vector
- 1.3. Use scikit-learn to fit a logistic regression model
- 1.4. Report classification metric: accuracy

### Part 2, Regression
- 2.1. Begin with baselines for regression
- 2.2. Do train/validate/test split. 
- 2.3. Arrange data into X features matrix and y target vector
- 2.4. Do one-hot encoding
- 2.5. Use scikit-learn to fit a linear regression (or ridge regression) model
- 2.6. Report validation MAE and $R^2$

### Stretch Goals, Regression
- Make visualizations to explore relationships between features and target
- Try at least 3 feature combinations. You may select features manually, or automatically
- Report validation MAE and $R^2$ for each feature combination you try
- Report test MAE and $R^2$ for your final model
- Print or plot the coefficients for the features in your model

In [1]:
# If you're in Colab...
import sys
in_colab = 'google.colab' in sys.modules

if in_colab:
    !pip install category_encoders==2.0.0
    !pip install pandas-profiling==2.3.0
    !pip install plotly==4.1.1

# Part 1, Classification: Predict Blood Donations 🚑
Our dataset is from a mobile blood donation vehicle in Taiwan. The Blood Transfusion Service Center drives to different universities and collects blood as part of a blood drive.

The goal is to predict whether the donor made a donation in March 2007, using information about each donor's history.

Good data-driven systems for tracking and predicting donations and supply needs can improve the entire supply chain, making sure that more patients get the blood transfusions they need.

In [2]:
import pandas as pd

donors = pd.read_csv('https://archive.ics.uci.edu/ml/machine-learning-databases/blood-transfusion/transfusion.data')
assert donors.shape == (748,5)

donors = donors.rename(columns={
    'Recency (months)': 'months_since_last_donation', 
    'Frequency (times)': 'number_of_donations', 
    'Monetary (c.c. blood)': 'total_volume_donated', 
    'Time (months)': 'months_since_first_donation', 
    'whether he/she donated blood in March 2007': 'made_donation_in_march_2007'
})

## 1.1. Begin with baselines

What accuracy score would you get here with a "majority class baseline"?
 
(You don't need to split the data into train and test sets yet. You can answer this question either with a scikit-learn function or with a pandas function.)

In [5]:
donors.made_donation_in_march_2007.value_counts(normalize=True)

0    0.762032
1    0.237968
Name: made_donation_in_march_2007, dtype: float64

In [ ]:
# with our baseline, we have an accuracy of 76%

## 1.2. Do train/test split. Arrange data into X features matrix and y target vector

Do these steps in either order.

Split randomly. Use scikit-learn's train/test split function. Include 75% of the data in the train set, and hold out 25% for the test set.

In [7]:
# checking if my data needs any cleaning
donors.isna().sum()

months_since_last_donation     0
number_of_donations            0
total_volume_donated           0
months_since_first_donation    0
made_donation_in_march_2007    0
dtype: int64

In [8]:
donors.head(20)

months_since_last_donation  number_of_donations  total_volume_donated  \
0                            2                   50                 12500   
1                            0                   13                  3250   
2                            1                   16                  4000   
3                            2                   20                  5000   
4                            1                   24                  6000   
5                            4                    4                  1000   
6                            2                    7                  1750   
7                            1                   12                  3000   
8                            2                    9                  2250   
9                            5                   46                 11500   
10                           4                   23                  5750   
11                           0                    3                   750   
12                           2                   10                  2500   
13                           1                   13                  3250   
14                           2                    6                  1500   
15                           2                    5                  1250   
16                           2                   14                  3500   
17                           2                   15                  3750   
18                           2                    6                  1500   
19                           2                    3                   750   

    months_since_first_donation  made_donation_in_march_2007  
0                            98                            1  
1                            28                            1  
2                            35                            1  
3                            45                            1  
4                            77                            0  
5                             4                            0  
6                            14                            1  
7                            35                            0  
8                            22                            1  
9                            98                            1  
10                           58                            0  
11                            4                            0  
12                           28                            1  
13                           47                            0  
14                           15                            1  
15                           11                            1  
16                           48                            1  
17                           49                            1  
18                           15                            1  
19                            4                            1

In [10]:
import pandas_profiling
donors.profile_report()

In [13]:
# seems like a pretty clean data set. now for train/test split.

import numpy as np

mask = np.random.randn(len(donors)) < 0.8
train = donors[mask]
test = donors[~mask]
print(train.describe())
test.describe()

       months_since_last_donation  number_of_donations  total_volume_donated  \
count                  604.000000           604.000000            604.000000   
mean                     9.753311             5.559603           1389.900662   
std                      8.328281             6.044727           1511.181868   
min                      0.000000             1.000000            250.000000   
25%                      2.750000             2.000000            500.000000   
50%                      9.000000             4.000000           1000.000000   
75%                     14.000000             7.000000           1750.000000   
max                     74.000000            50.000000          12500.000000   

       months_since_first_donation  made_donation_in_march_2007  
count                   604.000000                   604.000000  
mean                     34.620861                     0.236755  
std                      24.146395                     0.425443  
min            

months_since_last_donation  number_of_donations  total_volume_donated  \
count                  144.000000           144.000000            144.000000   
mean                     8.472222             5.326389           1331.597222   
std                      6.966397             4.898737           1224.684154   
min                      0.000000             1.000000            250.000000   
25%                      2.750000             2.000000            500.000000   
50%                      4.000000             4.000000           1000.000000   
75%                     14.000000             7.250000           1812.500000   
max                     39.000000            34.000000           8500.000000   

       months_since_first_donation  made_donation_in_march_2007  
count                   144.000000                   144.000000  
mean                     32.861111                     0.243056  
std                      25.357200                     0.430426  
min                       2.000000                     0.000000  
25%                      14.000000                     0.000000  
50%                      28.000000                     0.000000  
75%                      50.500000                     0.000000  
max                      98.000000                     1.000000

In [19]:
y_train = train['made_donation_in_march_2007']
y_test = test['made_donation_in_march_2007']
X_train = train.drop(columns='made_donation_in_march_2007')
X_test = test.drop(columns='made_donation_in_march_2007')
print(y_train.head())
print(X_train.head())
X_test.head()

0    1
1    1
2    1
4    0
6    1
Name: made_donation_in_march_2007, dtype: int64
   months_since_last_donation  number_of_donations  total_volume_donated  \
0                           2                   50                 12500   
1                           0                   13                  3250   
2                           1                   16                  4000   
4                           1                   24                  6000   
6                           2                    7                  1750   

   months_since_first_donation  
0                           98  
1                           28  
2                           35  
4                           77  
6                           14  


months_since_last_donation  number_of_donations  total_volume_donated  \
3                            2                   20                  5000   
5                            4                    4                  1000   
12                           2                   10                  2500   
13                           1                   13                  3250   
15                           2                    5                  1250   

    months_since_first_donation  
3                            45  
5                             4  
12                           28  
13                           47  
15                           11

In [16]:
print(y_train.shape)
print(X_train.shape)
print(X_test.shape)

(604,)
(604, 4)
(144, 4)


## 1.3. Use scikit-learn to fit a logistic regression model

You may use any number of features

In [18]:
from sklearn.linear_model import LogisticRegression
model = LogisticRegression().fit(X_train, y_train)
model.score(X_train, y_train)

0.7764900662251656

## 1.4. Report classification metric: accuracy

What is your model's accuracy on the test set?

Don't worry if your model doesn't beat the mean baseline. That's okay!

_"The combination of some data and an aching desire for an answer does not ensure that a reasonable answer can be extracted from a given body of data."_ —[John Tukey](https://en.wikiquote.org/wiki/John_Tukey)



In [20]:
model.score(X_test, y_test)

0.7708333333333334

# Part 2, Regression: Predict home prices in Ames, Iowa 🏠

You'll use historical housing data. There's a data dictionary at the bottom of the notebook. 

Run this code cell to load the dataset:





In [21]:
import pandas as pd
URL = 'https://drive.google.com/uc?export=download&id=1522WlEW6HFss36roD_Cd9nybqSuiVcCK'
homes = pd.read_csv(URL)
assert homes.shape == (2904, 47)

## 2.1. Begin with baselines

What is the Mean Absolute Error and R^2 score for a mean baseline?

In [22]:
homes.profile_report()

In [29]:
from sklearn.metrics import mean_absolute_error 
from sklearn.metrics import r2_score
import statistics

y_true = homes.SalePrice
y_pred = []
for _ in range(len(homes)):
    y_pred.append(homes.SalePrice.sum() / len(homes))
    
print(y_true.head())
print(y_pred[:10])

0    215000
1    105000
2    172000
3    244000
4    189900
Name: SalePrice, dtype: int64
[180383.689738292, 180383.689738292, 180383.689738292, 180383.689738292, 180383.689738292, 180383.689738292, 180383.689738292, 180383.689738292, 180383.689738292, 180383.689738292]


In [30]:
mae = mean_absolute_error(y_true, y_pred)
r2 = r2_score(y_true, y_pred)
print('Mean absolute error:', mae)
print('R^2 score:', r2)

Mean absolute error: 58149.92774120811
R^2 score: 0.0


## 2.2. Do train/test split

Train on houses sold in the years 2006 - 2008. (1,920 rows)

Validate on house sold in 2009. (644 rows)

Test on houses sold in 2010. (340 rows)

In [37]:
mask = homes[(homes['Yr_Sold'] >= 2006) & (homes['Yr_Sold'] <= 2008)]
X_train = mask.drop(columns='SalePrice')
y_train = mask['SalePrice']

mask = homes[homes['Yr_Sold'] == 2009]
X_val = mask.drop(columns='SalePrice')
y_val = mask['SalePrice']

mask = homes[homes['Yr_Sold'] == 2010]
X_test = mask.drop(columns='SalePrice')
y_test = mask['SalePrice']

assert(len(X_train) == 1920)
assert(len(X_val) == 644)
assert(len(X_test) == 340)

## 2.3. Arrange data into X features matrix and y target vector

Select at least one numeric feature and at least one categorical feature.

Otherwise, you many choose whichever features and however many you want.

In [38]:
# some of the features that had high correlation with sale price from the profile report
numeric_features = ['1st_Flr_SF', 'Full_Bath', 'Gr_Liv_Area', 'Overall_Qual',
            'TotRms_AbvGrd', 'Year_Built', 'Year_Remod/Add', 'Yr_Sold']


## 2.4. Do one-hot encoding

Encode your categorical feature(s).

In [40]:
import category_encoders as ce 
from sklearn.preprocessing import StandardScaler

categorical_features = ['Foundation']
features = categorical_features + numeric_features

X_train_subset = X_train[features]
X_val_subset = X_val[features]

encoder = ce.OneHotEncoder(use_cat_names=True)
X_train_encoded = encoder.fit_transform(X_train_subset)
X_val_encoded = encoder.transform(X_val_subset)

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train_encoded)
X_val_scaled = scaler.transform(X_val_encoded)

## 2.5. Use scikit-learn to fit a linear regression (or ridge regression) model
Fit your model.

In [41]:
from sklearn.linear_model import LinearRegression

model = LinearRegression(n_jobs = -1).fit(X_train_scaled, y_train)
print('Validation Accuracy', model.score(X_val_scaled, y_val))

Validation Accuracy 0.8079037337892556


## 2.6. Report validation MAE and $R^2$

What is your model's Mean Absolute Error and $R^2$ score on the validation set?

In [44]:
print('Mean absolute error:', mean_absolute_error(model.predict(X_val_scaled), y_val))
print('R^2 score:', r2_score(model.predict(X_val_scaled), y_val))

Mean absolute error: 24526.46253969916
R^2 score: 0.7421918839344758


# Stretch Goals, Regression
- Make visualizations to explore relationships between features and target
- Try at least 3 feature combinations. You may select features manually, or automatically
- Report validation MAE and $R^2$ for each feature combination you try
- Report test MAE and $R^2$ for your final model
- Print or plot the coefficients for the features in your model

# Data Dictionary 

Here's a description of the data fields:

```
1st_Flr_SF: First Floor square feet

Bedroom_AbvGr: Bedrooms above grade (does NOT include basement bedrooms)

Bldg_Type: Type of dwelling
		
       1Fam	Single-family Detached	
       2FmCon	Two-family Conversion; originally built as one-family dwelling
       Duplx	Duplex
       TwnhsE	Townhouse End Unit
       TwnhsI	Townhouse Inside Unit
       
Bsmt_Half_Bath: Basement half bathrooms

Bsmt_Full_Bath: Basement full bathrooms

Central_Air: Central air conditioning

       N	No
       Y	Yes
		
Condition_1: Proximity to various conditions
	
       Artery	Adjacent to arterial street
       Feedr	Adjacent to feeder street	
       Norm	Normal	
       RRNn	Within 200' of North-South Railroad
       RRAn	Adjacent to North-South Railroad
       PosN	Near positive off-site feature--park, greenbelt, etc.
       PosA	Adjacent to postive off-site feature
       RRNe	Within 200' of East-West Railroad
       RRAe	Adjacent to East-West Railroad
	
Condition_2: Proximity to various conditions (if more than one is present)
		
       Artery	Adjacent to arterial street
       Feedr	Adjacent to feeder street	
       Norm	Normal	
       RRNn	Within 200' of North-South Railroad
       RRAn	Adjacent to North-South Railroad
       PosN	Near positive off-site feature--park, greenbelt, etc.
       PosA	Adjacent to postive off-site feature
       RRNe	Within 200' of East-West Railroad
       RRAe	Adjacent to East-West Railroad
       
 Electrical: Electrical system

       SBrkr	Standard Circuit Breakers & Romex
       FuseA	Fuse Box over 60 AMP and all Romex wiring (Average)	
       FuseF	60 AMP Fuse Box and mostly Romex wiring (Fair)
       FuseP	60 AMP Fuse Box and mostly knob & tube wiring (poor)
       Mix	Mixed
       
 Exter_Cond: Evaluates the present condition of the material on the exterior
		
       Ex	Excellent
       Gd	Good
       TA	Average/Typical
       Fa	Fair
       Po	Poor
 
 Exter_Qual: Evaluates the quality of the material on the exterior 
		
       Ex	Excellent
       Gd	Good
       TA	Average/Typical
       Fa	Fair
       Po	Poor
		
Exterior_1st: Exterior covering on house

       AsbShng	Asbestos Shingles
       AsphShn	Asphalt Shingles
       BrkComm	Brick Common
       BrkFace	Brick Face
       CBlock	Cinder Block
       CemntBd	Cement Board
       HdBoard	Hard Board
       ImStucc	Imitation Stucco
       MetalSd	Metal Siding
       Other	Other
       Plywood	Plywood
       PreCast	PreCast	
       Stone	Stone
       Stucco	Stucco
       VinylSd	Vinyl Siding
       Wd Sdng	Wood Siding
       WdShing	Wood Shingles
	
Exterior_2nd: Exterior covering on house (if more than one material)

       AsbShng	Asbestos Shingles
       AsphShn	Asphalt Shingles
       BrkComm	Brick Common
       BrkFace	Brick Face
       CBlock	Cinder Block
       CemntBd	Cement Board
       HdBoard	Hard Board
       ImStucc	Imitation Stucco
       MetalSd	Metal Siding
       Other	Other
       Plywood	Plywood
       PreCast	PreCast
       Stone	Stone
       Stucco	Stucco
       VinylSd	Vinyl Siding
       Wd Sdng	Wood Siding
       WdShing	Wood Shingles
       
Foundation: Type of foundation
		
       BrkTil	Brick & Tile
       CBlock	Cinder Block
       PConc	Poured Contrete	
       Slab	Slab
       Stone	Stone
       Wood	Wood
		
Full_Bath: Full bathrooms above grade

Functional: Home functionality (Assume typical unless deductions are warranted)

       Typ	Typical Functionality
       Min1	Minor Deductions 1
       Min2	Minor Deductions 2
       Mod	Moderate Deductions
       Maj1	Major Deductions 1
       Maj2	Major Deductions 2
       Sev	Severely Damaged
       Sal	Salvage only
		
Gr_Liv_Area: Above grade (ground) living area square feet
        
Half_Bath: Half baths above grade

Heating: Type of heating
		
       Floor	Floor Furnace
       GasA	Gas forced warm air furnace
       GasW	Gas hot water or steam heat
       Grav	Gravity furnace	
       OthW	Hot water or steam heat other than gas
       Wall	Wall furnace
		
Heating_QC: Heating quality and condition

       Ex	Excellent
       Gd	Good
       TA	Average/Typical
       Fa	Fair
       Po	Poor

House_Style: Style of dwelling
	
       1Story	One story
       1.5Fin	One and one-half story: 2nd level finished
       1.5Unf	One and one-half story: 2nd level unfinished
       2Story	Two story
       2.5Fin	Two and one-half story: 2nd level finished
       2.5Unf	Two and one-half story: 2nd level unfinished
       SFoyer	Split Foyer
       SLvl	Split Level

Kitchen_AbvGr: Kitchens above grade

Kitchen_Qual: Kitchen quality

       Ex	Excellent
       Gd	Good
       TA	Typical/Average
       Fa	Fair
       Po	Poor

LandContour: Flatness of the property

       Lvl	Near Flat/Level	
       Bnk	Banked - Quick and significant rise from street grade to building
       HLS	Hillside - Significant slope from side to side
       Low	Depression
		
Land_Slope: Slope of property
		
       Gtl	Gentle slope
       Mod	Moderate Slope	
       Sev	Severe Slope

Lot_Area: Lot size in square feet

Lot_Config: Lot configuration

       Inside	Inside lot
       Corner	Corner lot
       CulDSac	Cul-de-sac
       FR2	Frontage on 2 sides of property
       FR3	Frontage on 3 sides of property

Lot_Shape: General shape of property

       Reg	Regular	
       IR1	Slightly irregular
       IR2	Moderately Irregular
       IR3	Irregular

MS_SubClass: Identifies the type of dwelling involved in the sale.	

        20	1-STORY 1946 & NEWER ALL STYLES
        30	1-STORY 1945 & OLDER
        40	1-STORY W/FINISHED ATTIC ALL AGES
        45	1-1/2 STORY - UNFINISHED ALL AGES
        50	1-1/2 STORY FINISHED ALL AGES
        60	2-STORY 1946 & NEWER
        70	2-STORY 1945 & OLDER
        75	2-1/2 STORY ALL AGES
        80	SPLIT OR MULTI-LEVEL
        85	SPLIT FOYER
        90	DUPLEX - ALL STYLES AND AGES
       120	1-STORY PUD (Planned Unit Development) - 1946 & NEWER
       150	1-1/2 STORY PUD - ALL AGES
       160	2-STORY PUD - 1946 & NEWER
       180	PUD - MULTILEVEL - INCL SPLIT LEV/FOYER
       190	2 FAMILY CONVERSION - ALL STYLES AND AGES

MS_Zoning: Identifies the general zoning classification of the sale.
		
       A	Agriculture
       C	Commercial
       FV	Floating Village Residential
       I	Industrial
       RH	Residential High Density
       RL	Residential Low Density
       RP	Residential Low Density Park 
       RM	Residential Medium Density

Mas_Vnr_Type: Masonry veneer type

       BrkCmn	Brick Common
       BrkFace	Brick Face
       CBlock	Cinder Block
       None	None
       Stone	Stone

Mo_Sold: Month Sold (MM)

Neighborhood: Physical locations within Ames city limits

       Blmngtn	Bloomington Heights
       Blueste	Bluestem
       BrDale	Briardale
       BrkSide	Brookside
       ClearCr	Clear Creek
       CollgCr	College Creek
       Crawfor	Crawford
       Edwards	Edwards
       Gilbert	Gilbert
       IDOTRR	Iowa DOT and Rail Road
       MeadowV	Meadow Village
       Mitchel	Mitchell
       Names	North Ames
       NoRidge	Northridge
       NPkVill	Northpark Villa
       NridgHt	Northridge Heights
       NWAmes	Northwest Ames
       OldTown	Old Town
       SWISU	South & West of Iowa State University
       Sawyer	Sawyer
       SawyerW	Sawyer West
       Somerst	Somerset
       StoneBr	Stone Brook
       Timber	Timberland
       Veenker	Veenker
			
Overall_Cond: Rates the overall condition of the house

       10	Very Excellent
       9	Excellent
       8	Very Good
       7	Good
       6	Above Average	
       5	Average
       4	Below Average	
       3	Fair
       2	Poor
       1	Very Poor

Overall_Qual: Rates the overall material and finish of the house

       10	Very Excellent
       9	Excellent
       8	Very Good
       7	Good
       6	Above Average
       5	Average
       4	Below Average
       3	Fair
       2	Poor
       1	Very Poor

Paved_Drive: Paved driveway

       Y	Paved 
       P	Partial Pavement
       N	Dirt/Gravel

Roof_Matl: Roof material

       ClyTile	Clay or Tile
       CompShg	Standard (Composite) Shingle
       Membran	Membrane
       Metal	Metal
       Roll	Roll
       Tar&Grv	Gravel & Tar
       WdShake	Wood Shakes
       WdShngl	Wood Shingles

Roof_Style: Type of roof

       Flat	Flat
       Gable	Gable
       Gambrel	Gabrel (Barn)
       Hip	Hip
       Mansard	Mansard
       Shed	Shed

SalePrice: the sales price for each house

Sale_Condition: Condition of sale

       Normal	Normal Sale
       Abnorml	Abnormal Sale -  trade, foreclosure, short sale
       AdjLand	Adjoining Land Purchase
       Alloca	Allocation - two linked properties with separate deeds, typically condo with a garage unit	
       Family	Sale between family members
       Partial	Home was not completed when last assessed (associated with New Homes)

Sale_Type: Type of sale
		
       WD 	Warranty Deed - Conventional
       CWD	Warranty Deed - Cash
       VWD	Warranty Deed - VA Loan
       New	Home just constructed and sold
       COD	Court Officer Deed/Estate
       Con	Contract 15% Down payment regular terms
       ConLw	Contract Low Down payment and low interest
       ConLI	Contract Low Interest
       ConLD	Contract Low Down
       Oth	Other
	
Street: Type of road access to property

       Grvl	Gravel	
       Pave	Paved
       	
TotRms_AbvGrd: Total rooms above grade (does not include bathrooms)

Utilities: Type of utilities available
		
       AllPub	All public Utilities (E,G,W,& S)	
       NoSewr	Electricity, Gas, and Water (Septic Tank)
       NoSeWa	Electricity and Gas Only
       ELO	Electricity only	
	
Year_Built: Original construction date

Year_Remod/Add: Remodel date (same as construction date if no remodeling or additions)
						
Yr_Sold: Year Sold (YYYY)	

```